In [1]:
import importlib
import sys
import os
import torch
import numpy as np
from tqdm.notebook import tqdm
import torch

sys.path.insert(0, '..')
sys.path.insert(1, '../../..')
sys.path.insert(0, "../../src")  # src package


## Generate Train, Val, Test

In [2]:
from perturbation_logic.activity_pertubator import (
    split_prefix_suffix_readable,
    redo_last_activity_of_prefix)
from event_log_loader_service.event_log_loader import (get_train_test_val_datasets,
                                                       extract_feature_info)
np.random.seed(17)

csv_path="../../../data/Sepsis.csv"

properties = {
    'case_name' : 'case:concept:name',
    'concept_name' : 'concept:name',
    'timestamp_name' : 'time:timestamp',
    'time_since_case_start_column' : 'case_elapsed_time',
    'time_since_last_event_column' : 'event_elapsed_time',
    'day_in_week_column' : 'day_in_week',
    'seconds_in_day_column' : 'seconds_in_day',
    'min_suffix_size' : 5,
    'train_validation_size' : 0.15,
    'test_validation_size' : 0.2,
    'window_size' : 'auto',
    'categorical_columns' : ['concept:name', 'InfectionSuspected', 'org:group', 'DiagnosticBlood', 'DisfuncOrg', 'SIRSCritTachypnea', 'Hypotensie', 'SIRSCritHeartRate', 'Infusion', 'DiagnosticArtAstrup', 'DiagnosticIC', 'DiagnosticSputum', 'DiagnosticLiquor', 'DiagnosticOther', 'SIRSCriteria2OrMore', 'DiagnosticXthorax', 'SIRSCritTemperature', 'DiagnosticUrinaryCulture', 'SIRSCritLeucos', 'Oligurie', 'DiagnosticLacticAcid', 'lifecycle:transition',
                             'Diagnose', 'Hypoxie', 'DiagnosticUrinarySediment', 'DiagnosticECG'],
    'continuous_columns' : ['case_elapsed_time', 'event_elapsed_time', 'day_in_week', 'seconds_in_day',
                            'Age', 'Leucocytes', 'CRP', 'LacticAcid'],
    'continuous_positive_columns' : []
    }


train_df, val_df, test_df,  = get_train_test_val_datasets(csv_path, properties)


print(len(train_df))

data_train = split_prefix_suffix_readable(
    train_df,
    case_column=properties["case_name"],
    activity_column=properties["concept_name"],
    min_suffix_size=2,
)

data_val = split_prefix_suffix_readable(
    val_df,
    case_column=properties["case_name"],
    activity_column=properties["concept_name"],
    min_suffix_size=2,
)

data_test = split_prefix_suffix_readable(
    test_df,
    case_column=properties["case_name"],
    activity_column=properties["concept_name"],
    min_suffix_size=2,
)

torch.save(data_train, '../../../perturbed_data/sepsis/train.pkl')
torch.save(data_val, '../../../perturbed_data/sepsis/val.pkl')
torch.save(data_test, '../../../perturbed_data/sepsis/test.pkl')


#display(train_df)

#extract feature info
feature_info = extract_feature_info(val_df, properties)


13509


# Create perturbed Datasets

In [6]:
# Last Event Attack
from perturbation_logic.feature_attacks import last_event_attack

# Reset data_val_copy for feature attacks
data_val_copy = data_val.copy()

# Attacks the last event of each prefix
data_pert_last = last_event_attack(
    data=data_val_copy,
    properties=properties,
    feature_info=feature_info,
    attackable_features=['concept:name', 'InfectionSuspected', 'org:group', 'DiagnosticBlood', 'DisfuncOrg', 'SIRSCritTachypnea', 'Hypotensie', 'SIRSCritHeartRate', 'Infusion', 'DiagnosticArtAstrup', 'DiagnosticIC', 'DiagnosticSputum', 'DiagnosticLiquor', 'DiagnosticOther', 'SIRSCriteria2OrMore', 'DiagnosticXthorax', 'SIRSCritTemperature', 'DiagnosticUrinaryCulture', 'SIRSCritLeucos', 'Oligurie', 'DiagnosticLacticAcid', 'lifecycle:transition',
                             'Diagnose', 'Hypoxie', 'DiagnosticUrinarySediment', 'DiagnosticECG', 'Age', 'Leucocytes', 'CRP', 'LacticAcid'],
    num_of_features_to_attack=5,
    magnitude=0.4,
    feature_range_scope='lokal',
    random_seed=17
)

torch.save(data_pert_last, '../../../perturbed_data/sepsis/last_event_attack.pkl')

In [7]:
# Random Event Attack
from perturbation_logic.feature_attacks import random_event_attack

# Attacks random events in each prefix with probability p
data_val_copy = data_val.copy()  
data_pert_random = random_event_attack(
    data=data_val_copy,
    properties=properties,
    feature_info=feature_info,
    attackable_features=['concept:name', 'InfectionSuspected', 'org:group', 'DiagnosticBlood', 'DisfuncOrg', 'SIRSCritTachypnea', 'Hypotensie', 'SIRSCritHeartRate', 'Infusion', 'DiagnosticArtAstrup', 'DiagnosticIC', 'DiagnosticSputum', 'DiagnosticLiquor', 'DiagnosticOther', 'SIRSCriteria2OrMore', 'DiagnosticXthorax', 'SIRSCritTemperature', 'DiagnosticUrinaryCulture', 'SIRSCritLeucos', 'Oligurie', 'DiagnosticLacticAcid', 'lifecycle:transition',
                             'Diagnose', 'Hypoxie', 'DiagnosticUrinarySediment', 'DiagnosticECG', 'Age', 'Leucocytes', 'CRP', 'LacticAcid'],
    num_of_features_to_attack=4,
    event_attack_probability=0.5,
    magnitude=0.5,
    feature_range_scope='local',
    random_seed=17
)

torch.save(data_pert_random, '../../../perturbed_data/sepsis/random_event_attack.pkl')

In [8]:
# Apply "redo last activity" augmentation to each prefix/suffix pair

data_val_copy = data_val.copy()  # Reset again
data_pert = {}
for key, (prefix_df, suffix_df) in data_val_copy.items():
    new_prefix, new_suffix = redo_last_activity_of_prefix(
        prefix_df,
        suffix_df,
        properties=properties,
    )
    data_pert[key] = (new_prefix, new_suffix)


torch.save(data_pert, '../../../perturbed_data/sepsis/redo_pert.pkl')


/home/chair/henryks_students/leon_urny/Robustness-in-suffix-prediction/robustness/perturbator/sepsis/../perturbation_logic/structural_attacks.py:191: FutureWarning: The behavior of DataFrame concatenation with empty or all-NA entries is deprecated. In a future version, this will no longer exclude empty or all-NA columns when determining the result dtypes. To retain the old behavior, exclude the relevant entries before the concat operation.
  updated_prefix = pd.concat([updated_prefix, duplicated_event.to_frame().T], ignore_index=True)
/home/chair/henryks_students/leon_urny/Robustness-in-suffix-prediction/robustness/perturbator/sepsis/../perturbation_logic/structural_attacks.py:191: FutureWarning: The behavior of DataFrame concatenation with empty or all-NA entries is deprecated. In a future version, this will no longer exclude empty or all-NA columns when determining the result dtypes. To retain the old behavior, exclude the relevant entries before the concat operation.
  updated_prefi

# Compare changes

In [16]:
# Compare clean and perturbed datasets
from perturbation_logic.attack_impact_analyzer import highlight_feature_attack_impact

# Compare clean dataset with random event attack
highlight_feature_attack_impact(
    clean_data_path='../../../perturbed_data/sepsis/val.pkl',
    perturbed_data_path='../../../perturbed_data/sepsis/last_event_attack.pkl',
    properties=properties
)

Loading clean dataset from: ../../../perturbed_data/sepsis/val.pkl
Loading perturbed dataset from: ../../../perturbed_data/sepsis/last_event_attack.pkl

Clean dataset has 1754 cases
Perturbed dataset has 1754 cases

COMPARISON RESULTS

Case: A, Prefix Length: 1
  ✓ No changes detected

Case: A, Prefix Length: 2
  [CHANGED] Found 1 event(s) with differences

  Event 1:
    Hypotensie:
      Clean:    nan
      Perturbed: False [CHANGED]
    DiagnosticIC:
      Clean:    nan
      Perturbed: True [CHANGED]


Case: A, Prefix Length: 3
  [CHANGED] Found 1 event(s) with differences

  Event 2:
    InfectionSuspected:
      Clean:    nan
      Perturbed: True [CHANGED]
    Infusion:
      Clean:    nan
      Perturbed: True [CHANGED]


Case: A, Prefix Length: 4
  [CHANGED] Found 1 event(s) with differences

  Event 3:
    DiagnosticArtAstrup:
      Clean:    nan
      Perturbed: True [CHANGED]
    DiagnosticUrinaryCulture:
      Clean:    nan
      Perturbed: True [CHANGED]


Case: A, Prefix

In [ ]:
# Compare clean and perturbed datasets
from perturbation_logic.attack_impact_analyzer import highlight_structural_attack_impact

# Compare clean dataset with random event attack
highlight_structural_attack_impact(
    clean_data_path='../../../perturbed_data/sepsis/val.pkl',
    perturbed_data_path='../../../perturbed_data/sepsis/redo_activity.pkl',
    properties=properties
)

Loading clean dataset from: ../../../perturbed_data/sepsis/val.pkl
Loading perturbed dataset from: ../../../perturbed_data/sepsis/redo_pert.pkl

Clean dataset has 1754 cases
Perturbed dataset has 1754 cases

STRUCTURAL ATTACK COMPARISON RESULTS

Case: A, Prefix Length: 1
Prefix
Activity_seq_clean = ['ER Registration']
Activity_seq_pert = ['ER Registration', 'ER Registration']
Case_elapsed_time_clean = [0.0]
Case_elapsed_time_pert = [0.0, 0.0]
Event_elapsed_time_clean = [nan]
Event_elapsed_time_pert = [nan, nan]
Day_in_week_clean = [2.0]
Day_in_week_pert = [2.0, 2.0]
Seconds_in_day_clean = [40541.0]
Seconds_in_day_pert = [40541.0, 40541.0]

===
suffix
Activity_seq_clean = ['Leucocytes', 'CRP', 'LacticAcid', 'ER Triage', 'ER Sepsis Triage', 'IV Liquid', 'IV Antibiotics', 'Admission NC', 'Leucocytes', 'CRP', 'Leucocytes', 'CRP', 'Leucocytes', 'CRP', 'CRP', 'Leucocytes', 'Leucocytes', 'CRP', 'Leucocytes', 'CRP', 'Release A', 'EOS', 'EOS', 'EOS', 'EOS', 'EOS']
Activity_seq_pert = ['Leucocyt